# NLP: LDA & Sentiment Analysis on Movie Reviews

## Load pretrained models or train from scratch?

In [25]:
import os
import pickle
use_pickled = input("Load pickled files/models? (y/n, defaults to y): ")
if use_pickled == 'n':
    use_pickled = False
else:
    use_pickled = True

pickled_dir = "pickled"


## Load the IMDB movie review dataset
This dataset is already separated into 25,000 negative and 25,000 positive reviews for a total of 50,000 reviews.

In [26]:
import pandas as pd

data = pd.read_csv('IMDB-Dataset.csv', error_bad_lines=False);

# split positive and negative sentiment reviews
pos_reviews = data[data.sentiment == "positive"]
neg_reviews = data[data.sentiment == "negative"]

pos_data = pos_reviews[['review']]
pos_data['index'] = pos_data.index
pos_documents = pos_data

neg_data = neg_reviews[['review']]
neg_data['index'] = neg_data.index
neg_documents = neg_data

# showing that the reviews were correctly split by sentiment
print(len(pos_documents))
print(pos_documents[:5])
print(len(neg_documents))
print(neg_documents[:5])

25000
                                              review  index
0  One of the other reviewers has mentioned that ...      0
1  A wonderful little production. <br /><br />The...      1
2  I thought this was a wonderful way to spend ti...      2
4  Petter Mattei's "Love in the Time of Money" is...      4
5  Probably my all-time favorite movie, a story o...      5
25000
                                               review  index
3   Basically there's a family where a little boy ...      3
7   This show was an amazing, fresh & innovative i...      7
8   Encouraged by the positive comments about this...      8
10  Phil the Alien is one of those quirky films wh...     10
11  I saw this movie when I was about 12 when it c...     11


## Initial Preprocessing: remove punctuation and convert everything to lowercase

In [27]:
# from nltk.corpus import stopwords
import re

# stop_words = list(set(stopwords.words('english')))

'''Positive Data'''
# Remove punctuation using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: x.lower())
'''Negative Data'''
# Remove punctuation using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: x.lower())

<>:8: DeprecationWarning: invalid escape sequence \.
<>:13: DeprecationWarning: invalid escape sequence \.
<>:8: DeprecationWarning: invalid escape sequence \.
<>:13: DeprecationWarning: invalid escape sequence \.
<>:8: DeprecationWarning: invalid escape sequence \.
<>:13: DeprecationWarning: invalid escape sequence \.
<ipython-input-27-6630992634b6>:8: DeprecationWarning: invalid escape sequence \.
  pos_documents['review_processed'] = pos_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
<ipython-input-27-6630992634b6>:13: DeprecationWarning: invalid escape sequence \.
  neg_documents['review_processed'] = neg_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))


## Generate World Cloud

Either loads the pickled objects from disk, or genereate a new word cloud objects and save it to disk.

In [28]:
from wordcloud import WordCloud

# load from pickled/wordcloud_pos and pickled/worldcloud_neg
if use_pickled:
    with open(os.path.join(pickled_dir, "wordcloud_pos"), 'rb') as f:
        wordcloud_pos = pickle.load(f)
    with open(os.path.join(pickled_dir, "wordcloud_neg"), 'rb') as f:
        wordcloud_neg = pickle.load(f)
else:
    # create a new wordcloud object for positive reviews, then write it to disk
    long_string_pos = " ".join(pos_documents.review_processed)
    wordcloud_pos = WordCloud().generate(long_string_pos)
    with open(os.path.join(pickled_dir, "wordcloud_pos"), 'wb+') as f:
        pickle.dump(wordcloud_pos, f)
    
    # create a new wordcloud object for negative reviews, then write it to disk
    long_string_neg = " ".join(neg_documents.review_processed)
    wordcloud_neg = WordCloud().generate(long_string_neg)
    with open(os.path.join(pickled_dir, "wordcloud_neg"), 'wb+') as f:
        pickle.dump(wordcloud_neg, f)

## Postitive Word Cloud

In [29]:
image = wordcloud_pos.to_image()
image.show()


## Negative Word Cloud

In [6]:
image = wordcloud_neg.to_image()
image.show()

## Stemming and Lematizing

In [31]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(2018)
import nltk

stemmer = SnowballStemmer("english")
def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))


def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

pos_proc_docs_fname = os.path.join(pickled_dir, "pos_processed_docs")
neg_proc_docs_fname = os.path.join(pickled_dir, "neg_processed_docs")
if use_pickled:
    with open(pos_proc_docs_fname, 'rb') as f1:
        pos_processed_documents = pickle.load(f1)
    with open(neg_proc_docs_fname, 'rb') as f2:
        neg_processed_documents = pickle.load(f2)
else:
    pos_processed_documents = pos_documents['review_processed'].map(preprocess)
    neg_processed_documents = neg_documents['review_processed'].map(preprocess)
    with open(pos_proc_docs_fname, 'wb+') as f1:
        pickle.dump(pos_processed_documents, f1)
    with open(neg_proc_docs_fname, 'wb+') as f2:
        pickle.dump(neg_processed_documents, f2)

print("Positive reviews after lemmatizing and stemming:")
print(len(pos_processed_documents))
print(pos_processed_documents[:10])

print("\nNegative reviews after lemmatizing and stemming:")
print(len(neg_processed_documents))
print(neg_processed_documents[:10])

Positive reviews after lemmatizing and stemming:
25000
0     [review, mention, watch, episod, hook, right, ...
1     [wonder, littl, product, film, techniqu, unass...
2     [think, wonder, spend, time, summer, weekend, ...
4     [petter, mattei, love, time, money, visual, st...
5     [probabl, time, favorit, movi, stori, selfless...
6     [sure, like, resurrect, date, seahunt, seri, t...
9     [like, origin, wrench, laughter, like, movi, y...
14    [fantast, movi, prison, famous, actor, georg, ...
16    [film, simpli, remak, film, fail, captur, flav...
18    [rememb, film, film, watch, cinema, pictur, da...
Name: review_processed, dtype: object

Negative reviews after lemmatizing and stemming:
25000
3     [basic, famili, littl, jake, think, zombi, clo...
7     [amaz, fresh, innov, idea, air, year, brillian...
8     [encourag, posit, comment, film, look, forward...
10    [phil, alien, quirki, film, humour, base, odd,...
11    [movi, come, recal, scariest, scene, bird, eat...
12    [boll

In [32]:
# Making Positive and Negative Dictionaries
pos_dictionary = gensim.corpora.Dictionary(pos_processed_documents)
count = 0
print("\nSome random positive words in our dictionary: ")
for k, v in pos_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 6:
        break    
neg_dictionary = gensim.corpora.Dictionary(neg_processed_documents)
count = 0
print("\nSome random negative words in our dictionary: ")
for k, v in neg_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 6:
        break


Some random positive words in our dictionary: 
0 accustom
1 agenda
2 agreement
3 appeal
4 aryan
5 audienc
6 away

Some random negative words in our dictionary: 
0 argu
1 basic
2 boogeyman
3 closet
4 decid
5 descent
6 dialog


## Remove Extreme Cases of Words
Words that are used less than 15 times or exist in more than half of the reviews are eliminated from the data set

In [33]:
#Removing Extreme Cases of Words
pos_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
pos_bow_corpus = [pos_dictionary.doc2bow(doc) for doc in pos_processed_documents] # corpus for topics that are seen as positive

neg_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
neg_bow_corpus = [neg_dictionary.doc2bow(doc) for doc in neg_processed_documents] # corpus for topics that are seen as negative

## Create the LDA Models

In [34]:
pos_lda_model_fname = os.path.join(pickled_dir, 'pos_lda_model')
neg_lda_model_fname = os.path.join(pickled_dir, 'neg_lda_model')
if use_pickled:
    pos_lda_model = gensim.models.LdaMulticore.load(pos_lda_model_fname)
    neg_lda_model = gensim.models.LdaMulticore.load(neg_lda_model_fname)

else:
    pos_lda_model = gensim.models.LdaMulticore(
        pos_bow_corpus, 
        num_topics=150, 
        id2word=pos_dictionary, 
        passes=10, 
        workers=6)

    neg_lda_model = gensim.models.LdaMulticore(
        neg_bow_corpus, 
        num_topics=150, 
        id2word=neg_dictionary, 
        passes=10, 
        workers=6)
    
    pos_lda_model.save(pos_lda_model_fname)
    neg_lda_model.save(neg_lda_model_fname)



In [11]:
# Viewing the LDA Model Topic Results
print("\nFirst Ten Positive Review Topics:")
for idx, topic in pos_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break
print("\nFirst Ten Negative Review Topics")
for idx, topic in neg_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break


First Ten Positive Review Topics:
Topic: 0 
Words: 0.016*"charact" + 0.015*"like" + 0.015*"great" + 0.014*"good" + 0.013*"actor" + 0.009*"stori" + 0.008*"see" + 0.008*"think" + 0.008*"watch" + 0.007*"play"
Topic: 1 
Words: 0.017*"scene" + 0.017*"watch" + 0.017*"time" + 0.013*"good" + 0.012*"great" + 0.011*"enjoy" + 0.010*"love" + 0.010*"chaplin" + 0.010*"comedi" + 0.009*"funni"
Topic: 2 
Words: 0.012*"charact" + 0.009*"play" + 0.008*"stori" + 0.007*"scene" + 0.006*"perform" + 0.005*"role" + 0.005*"director" + 0.005*"time" + 0.005*"great" + 0.004*"like"
Topic: 3 
Words: 0.022*"draw" + 0.015*"watch" + 0.011*"time" + 0.011*"like" + 0.010*"play" + 0.010*"good" + 0.009*"nanci" + 0.009*"wonder" + 0.009*"enjoy" + 0.008*"know"
Topic: 4 
Words: 0.020*"girl" + 0.013*"silli" + 0.012*"good" + 0.011*"enjoy" + 0.011*"play" + 0.010*"like" + 0.010*"villain" + 0.010*"thing" + 0.010*"peopl" + 0.010*"great"
Topic: 5 
Words: 0.018*"ring" + 0.014*"stori" + 0.009*"lord" + 0.009*"love" + 0.008*"emili" + 0.0

## Model Evaluation


### Perplexity: How "surprised" a model is of new data. (Given new data, how well does the model reproduce the statistics for that data)

In [12]:
from gensim.models import CoherenceModel
# compute perplexity, a measure of how good the model is. lower the better.
print('\nPositive LDA Model Perplexity: ', pos_lda_model.log_perplexity(pos_bow_corpus,))
print('\nNegative LDA Model Perplexity: ', neg_lda_model.log_perplexity(neg_bow_corpus))



Positive LDA Model Perplexity:  -8.29089888224202

Negative LDA Model Perplexity:  -8.329426279993639


### Coherence: Is the data related to other data in the data?

In [13]:
# Compute Coherence Score
pos_coherence_model_lda = CoherenceModel(model=pos_lda_model,texts=pos_processed_documents, dictionary=pos_dictionary, coherence='c_v')
pos_coherence_lda = pos_coherence_model_lda.get_coherence()
print('Positive LDA Model Coherence Score: ', pos_coherence_lda)

# Compute Coherence Score
neg_coherence_model_lda = CoherenceModel(model=neg_lda_model, texts=neg_processed_documents, dictionary=neg_dictionary, coherence='c_v')
neg_coherence_lda = neg_coherence_model_lda.get_coherence()
print('Negative LDA Model Coherence Score: ', neg_coherence_lda)

Positive LDA Model Coherence Score:  0.27257667675294167
Negative LDA Model Coherence Score:  0.2607593206815605


## TODO?: Mallet
MALLET is an another implementation of LDA that uses statistical sampling.

In [14]:
#import gensim

#'''Positive'''
# Download File: http://mallet.cs.umass.edu/dist/mallet-2.0.8.zip
#mallet_path = r'C:/MALLET/bin/mallet.bat' # update this path
#pos_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=pos_bow_corpus, num_topics=30, id2word=pos_dictionary)

# Show Topics
#print(pos_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#pos_coherence_model_ldamallet = CoherenceModel(model=pos_ldamallet, texts=pos_processed, dictionary=pos_dictionary, coherence='c_v')
#pos_coherence_ldamallet = pos_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', pos_coherence_ldamallet)

#'''Negative'''
#neg_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=neg_bow_corpus, num_topics=30, id2word=neg_dictionary)

# Show Topics
#print(neg_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#neg_coherence_model_ldamallet = CoherenceModel(model=neg_ldamallet, texts=neg_processed, dictionary=neg_dictionary, coherence='c_v')
#neg_coherence_ldamallet = neg_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', neg_coherence_ldamallet)

## Results: Data Science as an Art
* saliency: How notable or important is the term? The most salient term contribute the most information to all topics
* red bar: Frequency of the term for the given topic
* blue bar: Frequncey acorss the entire corpus
* lamba: low values -> rare, unique to topic. high values -> frequent, but probably not unique
* How many number of topcis should be generated?

In [15]:
import pyLDAvis
import pyLDAvis.gensim

# Visualize positive topic words
pyLDAvis.enable_notebook()
pos_vis = pyLDAvis.gensim.prepare(pos_lda_model, pos_bow_corpus, pos_dictionary)
pos_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
2      0.114052  0.066951       1        1  3.161438
89     0.143287  0.006279       2        1  2.250718
128   -0.096892  0.074383       3        1  1.949180
58     0.025842  0.113960       4        1  1.920331
92     0.054738  0.041481       5        1  1.809574
...         ...       ...     ...      ...       ...
79    -0.004025 -0.022300     146        1  0.385212
35    -0.030860 -0.012521     147        1  0.362624
115   -0.000043 -0.165438     148        1  0.305261
30    -0.040960 -0.083197     149        1  0.275148
66     0.022316 -0.250323     150        1  0.262148

[150 rows x 5 columns], topic_info=         Term          Freq         Total  Category  logprob  loglift
179      love  13437.000000  13437.000000   Default  30.0000  30.0000
26     episod   3015.000000   3015.000000   Default  29.0000  29.0000
492     music   5873.000000   5873.000000   Default  28.0000  28.0000
121     great  13721.000000  13721.000000   Default  27.0000  27.0000
291      like  20835.000000  20835.000000   Default  26.0000  26.0000
...       ...           ...           ...       ...      ...      ...
106      come     73.637108   8430.389648  Topic150  -4.3539   1.2036
1319  partner     48.971386    354.798889  Topic150  -4.7618   3.9637
1609    stage     51.787884    782.704956  Topic150  -4.7059   3.2284
2570    dynam     46.722424    235.871368  Topic150  -4.8088   4.3250
790    cooper     45.614765    318.047211  Topic150  -4.8328   4.0020

[9844 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
5450     30  0.978701   aamir
4769     69  0.256263   aaron
4769     71  0.141386   aaron
4769     81  0.123713   aaron
4769     94  0.459506   aaron
...     ...       ...     ...
2639     30  0.101108    zoom
2639     60  0.733031    zoom
2639    126  0.050554    zoom
7671     55  0.991437   zorro
4492     29  0.917350  zucker

[74985 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 90, 129, 59, 93, 110, 26, 64, 112, 47, 141, 124, 17, 49, 7, 38, 87, 139, 120, 113, 28, 77, 131, 150, 115, 85, 145, 111, 128, 2, 66, 30, 40, 86, 68, 114, 121, 43, 63, 57, 126, 22, 132, 10, 149, 75, 65, 107, 5, 97, 42, 62, 60, 23, 70, 136, 83, 48, 130, 14, 119, 146, 69, 61, 27, 122, 4, 16, 91, 45, 99, 6, 148, 51, 137, 41, 33, 46, 1, 9, 74, 79, 55, 12, 13, 101, 72, 20, 92, 76, 88, 103, 104, 8, 127, 102, 147, 135, 118, 105, 24, 56, 29, 108, 125, 21, 134, 143, 35, 81, 11, 71, 50, 106, 96, 123, 15, 34, 19, 84, 25, 109, 52, 142, 32, 89, 18, 44, 54, 100, 37, 138, 58, 140, 78, 144, 82, 53, 73, 94, 95, 98, 133, 117, 39, 80, 36, 116, 31, 67])

In [16]:
# Visualize negative topic words
pyLDAvis.enable_notebook()
neg_vis = pyLDAvis.gensim.prepare(neg_lda_model, neg_bow_corpus, neg_dictionary)
neg_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
57     0.167856  0.018656       1        1  3.085560
90     0.084044  0.062371       2        1  2.360736
54    -0.005697  0.112015       3        1  1.846986
16     0.025124  0.086430       4        1  1.817184
144   -0.037392  0.086956       5        1  1.665002
...         ...       ...     ...      ...       ...
13     0.005057 -0.086522     146        1  0.383001
88    -0.026967 -0.194094     147        1  0.379798
71    -0.066735 -0.107350     148        1  0.359598
65     0.021748 -0.048213     149        1  0.341517
48    -0.117103 -0.157625     150        1  0.325342

[150 rows x 5 columns], topic_info=         Term          Freq         Total  Category  logprob  loglift
1491     book   3306.000000   3306.000000   Default  30.0000  30.0000
60      funni   5228.000000   5228.000000   Default  29.0000  29.0000
218      game   1591.000000   1591.000000   Default  28.0000  28.0000
222      good  15562.000000  15562.000000   Default  27.0000  27.0000
509    comedi   3674.000000   3674.000000   Default  26.0000  26.0000
...       ...           ...           ...       ...      ...      ...
313      high     90.542145   3072.641846  Topic150  -4.2991   2.2036
606   serious     70.358559   1424.293091  Topic150  -4.5514   2.7202
850     state     66.842293   1062.737061  Topic150  -4.6026   2.9618
1577    crazi     59.059162    637.837830  Topic150  -4.7264   3.3485
79       star     71.228470   4321.063477  Topic150  -4.5391   1.6227

[9746 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
5660     50  0.180233   aaron
5660     72  0.138641   aaron
5660    107  0.665476   aaron
4269     62  0.929474    abba
7859    111  0.881711   abbey
...     ...       ...     ...
3002    118  0.093071    zone
7195     43  0.023576   zucco
7195    150  0.943033   zucco
7654     14  0.041720  zucker
7654     51  0.917831  zucker

[71732 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[58, 91, 55, 17, 145, 132, 34, 141, 12, 30, 93, 26, 105, 32, 90, 62, 112, 94, 136, 7, 102, 38, 22, 96, 11, 52, 128, 95, 111, 85, 135, 63, 6, 101, 149, 3, 29, 134, 31, 35, 47, 138, 4, 28, 108, 25, 146, 148, 15, 144, 122, 123, 113, 1, 100, 120, 76, 107, 133, 119, 137, 110, 10, 51, 130, 53, 36, 81, 98, 69, 80, 142, 82, 65, 9, 84, 50, 131, 40, 104, 71, 129, 114, 78, 92, 44, 79, 70, 109, 83, 5, 88, 117, 74, 77, 41, 20, 23, 48, 18, 115, 124, 64, 16, 99, 56, 140, 126, 125, 46, 21, 60, 13, 27, 139, 59, 73, 86, 87, 2, 42, 43, 67, 147, 127, 8, 103, 150, 61, 37, 57, 19, 97, 118, 121, 24, 106, 54, 68, 143, 75, 33, 45, 116, 39, 14, 89, 72, 66, 49])

In [35]:
def get_sentiment(text):
    count = 0
    pos_score = 0
    neg_score = 0
    #get what positive topics might be related
    bow_vector = pos_dictionary.doc2bow(preprocess(text))
    
    for idx, score in sorted(pos_lda_model[bow_vector], key=lambda tup:-1*tup[1]):
        count+=1
        pos_score += score
        if count > 2:
            break
    pos_score = pos_score/3
    pos_score *= 100
    
    count = 0
    #get what negative topics might be related
    bow_vector = neg_dictionary.doc2bow(preprocess(text))
    for idx, score in sorted(neg_lda_model[bow_vector], key=lambda tup:-1*tup[1]):    
        neg_score += score
        count+=1
        if count > 2:
            break
    neg_score = neg_score/3
    neg_score *= 100
    
    result = 0
    if pos_score>neg_score:
        result = (pos_score - neg_score)/(pos_score + neg_score)
        result *= 100
        result = 50 + (result*2)
        return result
    else:
        result = (neg_score - pos_score)/(pos_score + neg_score)
        result *= 100
        result = 50+(result*2)
        return result

In [36]:
def get_general_sentiment(text):
    pos_score = 0
    neg_score = 0
    #get what positive topics might be related
    bow_vector = pos_dictionary.doc2bow(preprocess(text))
    
    for idx, score in sorted(pos_lda_model[bow_vector], key=lambda tup:-1*tup[1]):
        pos_score += score
        break;
   
    #get what negative topics might be related
    bow_vector = neg_dictionary.doc2bow(preprocess(text))
    for idx, score in sorted(neg_lda_model[bow_vector], key=lambda tup:-1*tup[1]):    
        neg_score += score
        break;

    if pos_score>neg_score:
        return "positive"
    else:
        return "negative"

In [38]:
unseen_movie_description = input("Please enter a movie description to analyze: ")
result = round(get_sentiment(unseen_movie_description), 3)
print("\nWe predict that opinions on this movie are generally {}.".format(get_general_sentiment(unseen_movie_description)))
print("\nWe predict that this movie has a rating of ~{}%.".format(result))


We predict that opinions on this movie are generally positive.

We predict that this movie has a rating of ~58.522%.
